In [ ]:
# Setup

In [1]:
import numpy as np
import random
import math
from math import log, sqrt, ceil
import pandas as pd
import geopandas as gp 
from shapely.geometry import Point
import json
from bokeh.io import output_notebook, show, output_file, curdoc
from bokeh.plotting import figure
from bokeh.palettes import brewer
from bokeh.tile_providers import get_provider, Vendors
from bokeh.models import TapTool,GeoJSONDataSource, TextInput, LinearColorMapper,LabelSet, ColorBar,ColumnDataSource,Button, Slider, HoverTool,CDSView, GroupFilter, FixedTicker, FuncTickFormatter, RangeTool, ResetTool
from functools import partial
from bokeh.layouts import widgetbox, row, column, layout, gridplot
from datetime import datetime, timedelta, date
from bokeh.models.widgets import Tabs, Panel
from bokeh.models.glyphs import Patches

from collections import OrderedDict
from six.moves import cStringIO as StringIO
import calendar
from bokeh.layouts import gridplot

import matplotlib.pyplot as plt
import copy
import os
from patsy import dmatrices
import statsmodels.api as sm
import statsmodels.formula.api as smf

In [ ]:
# Data preparation

In [2]:
p = 0.15
YT_01 = pd.read_csv('Data/yellow_tripdata_2018-01.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_01 = pd.read_csv('Data/fhv_tripdata_2018-01.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
YT_02 = pd.read_csv('Data/yellow_tripdata_2018-02.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_02 = pd.read_csv('Data/fhv_tripdata_2018-02.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
YT_03 = pd.read_csv('Data/yellow_tripdata_2018-03.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_03 = pd.read_csv('Data/fhv_tripdata_2018-03.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
YT_09 = pd.read_csv('Data/yellow_tripdata_2017-09.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
YT_10 = pd.read_csv('Data/yellow_tripdata_2017-10.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
YT_11 = pd.read_csv('Data/yellow_tripdata_2017-11.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
YT_12 = pd.read_csv('Data/yellow_tripdata_2017-12.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_09 = pd.read_csv('Data/fhv_tripdata_2017-09.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_10 = pd.read_csv('Data/fhv_tripdata_2017-10.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_11 = pd.read_csv('Data/fhv_tripdata_2017-11.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)
FHV_12 = pd.read_csv('Data/fhv_tripdata_2017-12.csv',header=0,skiprows=lambda i: i>0 and random.random() > p)

In [3]:
YT = pd.concat([YT_01,YT_02,YT_03,YT_09,YT_10,YT_11,YT_12])
FHV = pd.concat([FHV_01,FHV_02, FHV_03, FHV_09, FHV_10, FHV_11, FHV_12])

In [4]:
Taxi = pd.concat([YT,FHV])

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [5]:
Taxi['Pickup_DateTime'] = pd.to_datetime(Taxi['Pickup_DateTime']) 
Taxi['Pickup_Hour'] = Taxi['Pickup_DateTime'].dt.hour
Taxi['Day_Week'] = Taxi['Pickup_DateTime'].dt.dayofweek
Taxi['Days'] = Taxi['Pickup_DateTime'].dt.day
Taxi['Pickup_Date'] = Taxi['Pickup_DateTime'].dt.date

In [6]:
locations = gp.read_file('Data/taxi_zones/taxi_zones.shx')
locations = locations.to_crs(epsg = 3857)
locations = locations.loc[:,['LocationID','borough','zone','geometry']]

/home/ubuntu/anaconda3/lib/python3.7/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))


In [7]:
colors = ['#fe6632','#fdba2c', '#8cc3d7', '#0085ff', '#0000cc']
bor_bound = gp.read_file('Data/Borough boundaries/geo_export_90fe914d-0ab3-46e0-8dad-c9f637a3a5bb.shx')
bor_bound = bor_bound.to_crs(epsg = 3857)
bor_bound = bor_bound.loc[:,['boro_name','geometry']]
bor_bound['color'] = colors
bor_categ = list(bor_bound['boro_name'])

points = [poly.centroid for poly in bor_bound['geometry']]

bor_json = json.loads(bor_bound.to_json())
bor_json_full = json.dumps(bor_json)
bor_geosource = GeoJSONDataSource(geojson = bor_json_full)

bor_center = pd.DataFrame(list(zip(bor_categ,points,colors)), columns =['boro_name','center', 'color']) 
bor_center = gp.GeoDataFrame(bor_center,geometry = 'center')

/home/ubuntu/anaconda3/lib/python3.7/site-packages/pyproj/crs.py:77: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method.
  return _prepare_from_string(" ".join(pjargs))


In [8]:
def bor_cat(category):
    bor_categ = bor_center[bor_center['boro_name'] == category]
    #Read data to json.
    bor_json = json.loads(bor_categ.to_json())
    #Convert to String like object.
    bor_json_full = json.dumps(bor_json)
    bor_geosource = GeoJSONDataSource(geojson = bor_json_full)
    return bor_geosource

In [9]:
Taxi = pd.merge(Taxi,locations,how = 'inner', left_on = 'PULocationID', right_on = 'LocationID')
Taxi.rename(columns={"borough": "PUborough", "zone": "PUzone", "geometry": "PUgeometry"},inplace = True)

Taxi = pd.merge(Taxi,locations,how = 'inner', left_on = 'DOLocationID', right_on = 'LocationID')
Taxi.rename(columns={"borough": "DOborough", "zone": "DOzone", "geometry": "DOgeometry"},inplace = True)

Taxi.drop(columns=['LocationID_x', 'LocationID_y'],inplace = True)

In [63]:
# global necessary variables for tab 3 visualisations
ranges_map = pd.DataFrame(Taxi.groupby(['company_name','PUzone','month']).size()).rename(columns={0: "PUNumber"})
ranges_map.reset_index(inplace = True)
max_numbUber = max(ranges_map.loc[ranges_map['company_name'] == 'Uber','PUNumber'])
max_numbYT = max(ranges_map.loc[ranges_map['company_name'] == 'YT','PUNumber'])
width_map = 700
height_map = 700
width_clock = 600
height_clock = 600
width_bubble = 600
height_bubble = 600
inner_radius = 90
outer_radius = 320
length = 24
big_angle = 2.0 * np.pi / (length+1)
small_angle = big_angle / 5
#series
series = pd.Series(np.arange(0,length))
# annular wedges
angles = np.pi/2 - big_angle/2 - series*big_angle

In [64]:
#this is for clock graph
def compare(a, b):
    if a > b:
        return "Uber>YellowTaxi"
    else:
        return "Uber<YellowTaxi"

In [65]:
def Ave_Day(a, b, num_days):
    if a == 0:
        return ceil(b/num_days[a])
    elif a == 1:
        return ceil(b/num_days[a])
    elif a == 2:
        return ceil(b/num_days[a])
    elif a == 3:
        return ceil(b/num_days[a])
    elif a == 4:
        return ceil(b/num_days[a])
    elif a == 5:
        return ceil(b/num_days[a])
    elif a == 6:
        return ceil(b/num_days[a])

In [66]:
def adjust_scale(df, scale, name):
    
    adj_pos = 0.5 
    n = 9
    
    df['AdjAveDayCount'] = np.ceil(df['AveDayCount'] * (40/scale))
    df['AdjPickupHourGroup'] = df['PickupHourGroup']+ adj_pos
    df['AdjColor'] = (df['AveDayCount']//(scale/8)).astype(int)
    df['company_name']='Uber'
    if(name == 'Uber'):
        df['AdjPosition'] = df['Day_Week'] - 0.15 + adj_pos
    else:
        df['AdjPosition'] = df['Day_Week'] + 0.15 + adj_pos
    
    return df

In [67]:
def map_data(selectedMonth):
    year = 2017
    mth = selectedMonth
    if(mth<5):
        mth = mth+8
    else:
        year = 2018
        mth = mth - 4
    Taxi_loc_full = Taxi.loc[(Taxi['month'] == mth)&(Taxi['year'] == year),:]
    Taxi_loc_full['Number'] = Taxi_loc_full.groupby(['PUborough','PUzone','company_name'])['PUgeometry'].transform('count')
    Taxi_uniq_PU = Taxi_loc_full.drop_duplicates(subset=['PUborough', 'PUzone','company_name'])
    Taxi_uniq_PU = Taxi_uniq_PU.loc[:,['PUborough','PUzone', 'PUgeometry', 'Number','company_name']]
    Taxi_uniq_PU['company_number'] = Taxi_uniq_PU.groupby(['PUborough','PUzone'])['company_name'].transform('count')
    Taxi_uniq_PU["rank"] = 1
    Taxi_uniq_PU.loc[Taxi_uniq_PU["company_number"] == 2,"rank"] = Taxi_uniq_PU.groupby(["PUborough","PUzone"])["Number"].rank("dense", ascending = False)
    
    
    #get rows only with rank = 1 (in case of two companies in same location it means that the map 
    #will plot the information of company with the prevaling number of PU. In case of one company in location the map 
    #will just plot the information of that company)

    Taxi_uniq_PU = Taxi_uniq_PU.loc[Taxi_uniq_PU['rank'] == 1]
    
    #convert to GeoDataFrame
    Taxi_geo = gp.GeoDataFrame(Taxi_uniq_PU,geometry = 'PUgeometry')
    
    #split the whole dataframe into two separate dataframes Uber and YT
    YT_geo = Taxi_geo.loc[Taxi_uniq_PU['company_name'] == 'YT']
    Uber_geo = Taxi_geo.loc[Taxi_uniq_PU['company_name'] == 'Uber']
    
    #Read data to json.
    YT_json = json.loads(YT_geo.to_json())
    Uber_json = json.loads(Uber_geo.to_json())
    #Convert to String like object.
    YT_json_full = json.dumps(YT_json)
    Uber_json_full = json.dumps(Uber_json)

    return YT_json_full,Uber_json_full

In [68]:
def location_data(selectedBor,selectedMonth):
    bor = selectedBor
    mth = selectedMonth
    year = 2017
    if(mth<5):
        mth = mth+8
    else:
        year = 2018
        mth = mth - 4
    Taxi_loc_full = Taxi.loc[(Taxi['PUborough'] == bor) & (Taxi['month'] == mth) &(Taxi['year'] == year),:]
    return Taxi_loc_full

In [69]:
def clock_graph(selectedBor,selectedMonth):
    Taxi_loc_full = location_data(selectedBor,selectedMonth)
    TaxiTimeCount = Taxi_loc_full.groupby(['Pickup_Hour','company_name'])['Pickup_DateTime'].agg('count').reset_index(name = 'count')
    TaxiTimeCount = TaxiTimeCount.pivot(index='Pickup_Hour', columns='company_name', values='count')
    TaxiTimeCount.fillna(0, inplace = True)
    TaxiTimeCount['Uber']=TaxiTimeCount['Uber']/calendar.monthrange(2018,selectedMonth)[1]
    TaxiTimeCount['YT']=TaxiTimeCount['YT']/calendar.monthrange(2018,selectedMonth)[1]
    TaxiTimeCount['Comparison'] = TaxiTimeCount.apply(lambda x : compare(x['Uber'],x['YT']),axis = 1)
    
    adjclock = 230/max(TaxiTimeCount['Uber'].max(),TaxiTimeCount['YT'].max())
    
    # annular start_angles
    start_angles = -big_angle+angles
    #uber start_angles
    ub_start_angl = -big_angle+angles+3*small_angle
    #uber end_angles
    ub_end_angl = -big_angle+angles+4*small_angle
    #YT start_angles
    YT_start_angl = -big_angle+angles+1*small_angle
    YT_end_angl = -big_angle+angles+2*small_angle
    
    #create full datasource (add needed columns)
    TaxiTimeCount['comparison_color'] = np.where(TaxiTimeCount['Comparison'] == 'Uber>YellowTaxi', '#1ebad6', '#febb1b')
    TaxiTimeCount['angles'] = angles
    TaxiTimeCount['start_angles'] = start_angles
    TaxiTimeCount['Uber_startangle'] = ub_start_angl
    TaxiTimeCount['Uber_endangle'] = ub_end_angl
    TaxiTimeCount['YT_startangle'] = YT_start_angl
    TaxiTimeCount['YT_endangle'] = YT_end_angl
    TaxiTimeCount['Uber_adjustedcount'] = adjclock*TaxiTimeCount['Uber']+90
    TaxiTimeCount['YT_adjustedcount'] = adjclock*TaxiTimeCount['YT']+90
    
    
    lblclock = (np.ceil(np.linspace (230,0,5)/adjclock)).astype(int)
    lblclockdf = pd.DataFrame(lblclock)
    lblclockdf.rename(columns={0:'label_num'}, inplace=True)
    lblclockdf['label_num']=lblclockdf['label_num'].astype(str)
    lblclockdf['radii']= np.linspace(320, 90, 5)

    return TaxiTimeCount,lblclockdf

In [76]:
def bubble_graph(selectedBor,selectedMonth):
    Taxi_loc_full = location_data(selectedBor,selectedMonth)
    
    TaxiDay = Taxi_loc_full[['Day_Week','Days']].drop_duplicates()
    
    num_days = []
    
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==0]))
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==1]))
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==2]))
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==3]))
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==4]))
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==5]))
    num_days.append(len(TaxiDay[TaxiDay['Day_Week']==6]))
    
    TaxiDayCount = Taxi_loc_full.groupby(['Day_Week','Pickup_Hour','company_name'])['Pickup_DateTime'].agg('count').reset_index(name = 'count')

    conditions = [(TaxiDayCount['Pickup_Hour']==0)|(TaxiDayCount['Pickup_Hour']==1),
              (TaxiDayCount['Pickup_Hour']==2)|(TaxiDayCount['Pickup_Hour']==3),
              (TaxiDayCount['Pickup_Hour']==4)|(TaxiDayCount['Pickup_Hour']==5),
              (TaxiDayCount['Pickup_Hour']==6)|(TaxiDayCount['Pickup_Hour']==7),
              (TaxiDayCount['Pickup_Hour']==8)|(TaxiDayCount['Pickup_Hour']==9),
              (TaxiDayCount['Pickup_Hour']==10)|(TaxiDayCount['Pickup_Hour']==11),
              (TaxiDayCount['Pickup_Hour']==12)|(TaxiDayCount['Pickup_Hour']==13),
              (TaxiDayCount['Pickup_Hour']==14)|(TaxiDayCount['Pickup_Hour']==15),
              (TaxiDayCount['Pickup_Hour']==16)|(TaxiDayCount['Pickup_Hour']==17),
              (TaxiDayCount['Pickup_Hour']==18)|(TaxiDayCount['Pickup_Hour']==19),
              (TaxiDayCount['Pickup_Hour']==20)|(TaxiDayCount['Pickup_Hour']==21),
              (TaxiDayCount['Pickup_Hour']==22)|(TaxiDayCount['Pickup_Hour']==23)]
    
    choices = [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11]
    TaxiDayCount['PickupHourGroup'] = np.select(conditions, choices)
    
    
    UberDayCount = TaxiDayCount[(TaxiDayCount['company_name'] == 'Uber')]
    YTDayCount = TaxiDayCount[(TaxiDayCount['company_name'] == 'YT')]
    UberDayCount = UberDayCount.groupby(['Day_Week','PickupHourGroup'])['count'].agg(np.sum).reset_index(name = 'sumcount')
    YTDayCount = YTDayCount.groupby(['Day_Week','PickupHourGroup'])['count'].agg(np.sum).reset_index(name = 'sumcount')
    
    UberDayCount['company_name']='Uber'
    UberDayCount['AveDayCount'] = ''
    UberDayCount['AdjAveDayCount'] = ''
    UberDayCount['AdjPosition'] = ''
    UberDayCount['AdjPickupHourGroup'] = ''
    UberDayCount['AdjColor'] = ''
    UberDayCount['Color'] = ''
    
    
    YTDayCount['company_name']='Yellow Taxi'
    YTDayCount['AveDayCount'] = ''
    YTDayCount['AdjAveDayCount'] = ''
    YTDayCount['AdjPosition'] = ''
    YTDayCount['AdjPickupHourGroup'] = ''
    YTDayCount['AdjColor'] = ''
    YTDayCount['Color'] = ''

    
    if((UberDayCount.empty == False)&(YTDayCount.empty == False)):
        UberDayCount['AveDayCount'] = UberDayCount.apply(lambda x: Ave_Day(x.Day_Week, x.sumcount,num_days), axis=1)
        YTDayCount['AveDayCount'] = YTDayCount.apply(lambda x: Ave_Day(x.Day_Week, x.sumcount,num_days), axis=1)
        adj_ave = max(UberDayCount['AveDayCount'].max(),YTDayCount['AveDayCount'].max())
        UberDayCount = adjust_scale(UberDayCount, adj_ave, 'Uber')
        YTDayCount = adjust_scale(YTDayCount, adj_ave, 'YT')        
    elif((UberDayCount.empty == False) &(YTDayCount.empty == True)):
        UberDayCount['AveDayCount'] = UberDayCount.apply(lambda x: Ave_Day(x.Day_Week, x.sumcount,num_days), axis=1)
        adj_ave = UberDayCount['AveDayCount'].max()
        UberDayCount = adjust_scale(UberDayCount, adj_ave,'Uber')
        YTDayCount.drop(YTDayCount.index, inplace=True)
    elif((UberDayCount.empty == True) &(YTDayCount.empty == False)):
        YTDayCount['AveDayCount'] = YTDayCount.apply(lambda x: Ave_Day(x.Day_Week, x.sumcount,num_days), axis=1)
        adj_ave = YTDayCount['AveDayCount'].max()
        YTDayCount = adjust_scale(YTDayCount, adj_ave, 'YT')
        UberDayCount.drop(UberDayCount.index, inplace=True)

    return UberDayCount,YTDayCount

In [71]:
Text_tab3 = figure(plot_width=600, plot_height=300,
           min_border=0, x_range=(0,100), y_range=(0,100), 
           toolbar_location=None, title="")

Text_tab3.text(x=1, y=20, text_font_size = "12pt", text=["""
This is an interactive tab, where you can:

1) Tap to choose a borough on a map to see the graphs change accordingly
2) Use a slider to select a month where 1 is Sep 2017 and 7 is March 2018
3) First graph on the bottom is a clock graph which illustrates the average 
    number of pick-ups for each hour in a day
4) Second graph on the bottom is a bubble chart which shows the average 
    number of pick-ups for every two hours and each day of the week
"""])


Text_tab3.title.text_font_size = "14pt"
Text_tab3.title.text_font_style = "bold"
Text_tab3.title.align = 'center'

Text_tab3.xaxis.visible = None
Text_tab3.yaxis.visible = None
Text_tab3.xgrid.grid_line_color = None
Text_tab3.ygrid.grid_line_color = None
Text_tab3.border_fill_color = None
Text_tab3.outline_line_color = None


In [85]:
months = [1,2,3,4,5,6,7]

#FUNCTIONS

def animate_update():
    month = month_slider.value + 1
    if month > months[-1]:
        month = months[0]
    month_slider.value = month
    

def update_map(attr, old, new):
    mth = month_slider.value
    YT_json_full,Uber_json_full = map_data(mth)
    YT_geosource.geojson = YT_json_full
    Uber_geosource.geojson = Uber_json_full
    
    
def map_slider_interactions(attr, old, new):
        mth = month_slider.value
        selected_index = bor_geosource.selected.indices[0]
        borough_name = bor_bound.iloc[selected_index]['boro_name'] 
        TaxiTimeCnt,lblclock = clock_graph(borough_name,mth)
        TaxiTimeCount.data = TaxiTimeCnt
        lblclockdf.data = lblclock
        UberDayCount,YTDayCount = bubble_graph(borough_name,mth)
        CUberDayCount.data = UberDayCount
        CYTDayCount.data = YTDayCount
        tap_borough.value = borough_name
        

callback_id = None
def animate():
    global callback_id
    if button.label == '► Play':
        button.label = '❚❚ Pause'
        callback_id = curdoc().add_periodic_callback(animate_update, 500)
    else:
        button.label = '► Play'
        curdoc().remove_periodic_callback(callback_id)  
        
################################################################################################################################################################
#MAP GRAPH

#initial values
YT_json_full,Uber_json_full = map_data(months[0])
YT_geosource = GeoJSONDataSource(geojson = YT_json_full)
Uber_geosource = GeoJSONDataSource(geojson = Uber_json_full)

#Define a sequential multi-hue color palette.
uber_pallete = brewer['PuBu'][8]
YT_pallete = brewer['YlOrBr'][8]

uber_pallete = uber_pallete[::-1]
YT_pallete = YT_pallete[::-1]

ub_ra_int = [int(i) for i in np.round(np.linspace(0,max_numbUber,num = 9))]
YT_ra_int = [int(i) for i in np.round(np.linspace(0,max_numbYT,num = 9))]
ub_ra_lb = [str(int(i)) for i in ub_ra_int]
YT_ra_lb = [str(int(i)) for i in YT_ra_int]


#Instantiate LinearColorMapper that linearly maps numbers in a range, into a sequence of colors.
cm_Uber = LinearColorMapper(palette = uber_pallete, low = 0, high = max_numbUber)
cm_YT = LinearColorMapper(palette = YT_pallete, low = 0, high = max_numbYT)

#Define custom tick labels for color bar.

ub_ticks = dict(zip(ub_ra_lb, ub_ra_lb))
YT_ticks = dict(zip(YT_ra_lb, YT_ra_lb))

ub_ticker = FixedTicker(ticks = ub_ra_int)
YT_ticker = FixedTicker(ticks = YT_ra_int)

#Create color bar. 
cb_uber = ColorBar(color_mapper = cm_Uber, label_standoff = 8,width = 500, height = 20,
border_line_color = None,location = (0,0), orientation = 'horizontal', major_label_overrides = ub_ticks,
ticker = ub_ticker,major_tick_line_color = 'black')

cb_YT = ColorBar(color_mapper = cm_YT, label_standoff = 8,width = 500, height = 20,
border_line_color = None,location = (0,-10), orientation = 'horizontal', major_label_overrides = YT_ticks,
ticker = YT_ticker,major_tick_line_color = 'black')

color_bar_YT = figure(height=100, width=600, toolbar_location=None, min_border=0, outline_line_color=None)
color_bar_YT.add_layout(cb_YT, 'below')

color_bar_Uber = figure(height=100, width=600, toolbar_location=None, min_border=0, outline_line_color=None)
color_bar_Uber.add_layout(cb_uber, 'below')


#Create figure object.

map_plot = figure(x_range=(-8269186.976031984, -8201155.123517304), y_range=(4935220.994445528, 5002970.251017523),
           plot_height = height_map, plot_width = width_map, tools = "")


tile_provider = get_provider(Vendors.STAMEN_TERRAIN)
map_plot.add_tile(tile_provider)
map_plot.xgrid.grid_line_color = None
map_plot.ygrid.grid_line_color = None
map_plot.xaxis.visible = None
map_plot.yaxis.visible = None

YT_patches = map_plot.patches('xs','ys', source = YT_geosource,fill_color = {'field' :'Number', 'transform' : cm_YT},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)

uber_patches = map_plot.patches('xs','ys', source = Uber_geosource,fill_color = {'field' :'Number', 'transform' : cm_Uber},
          line_color = 'black', line_width = 0.25, fill_alpha = 1)

bor_patches = map_plot.patches(xs='xs',ys='ys', line_color = 'color', source = bor_geosource, fill_color = None, line_width = 0.25)

for cat in bor_categ:
    bor_source = bor_cat(cat)
    map_plot.circle('x', 'y', size = 0, source =  bor_source, color = 'color', legend = cat)

selected_patches = Patches(fill_alpha = 0, fill_color = None)
nonselected_patches = Patches(fill_alpha = 1, fill_color = 'color')

bor_patches.selection_glyph = selected_patches
bor_patches.nonselection_glyph = nonselected_patches

hover_YT = HoverTool(renderers=[YT_patches],tooltips = [('Borough','@PUborough'),('Zone','@PUzone'),('Company','@company_name'),('Number of Pick Ups', '@Number')])
hover_Uber = HoverTool(renderers=[uber_patches],tooltips = [('Borough','@PUborough'),('Zone','@PUzone'),('Company','@company_name'),('Number of Pick Ups', '@Number')])    


# Add tap tool to select neighborhood on map
tap = TapTool(renderers=[bor_patches])

map_plot.add_tools(tap)
map_plot.add_tools(hover_YT)
map_plot.add_tools(hover_Uber)


#############################################################################################################################################

#CLOCK GRAPH
#initial value
TaxiTimeCount,lblclockdf = clock_graph(bor_categ[3],months[0])
TaxiTimeCount = ColumnDataSource(TaxiTimeCount)
lblclockdf = ColumnDataSource(lblclockdf)

Taxi_color = OrderedDict([
    ("Uber",   "#222233"),
    ("YellowTaxi", "#ff8400"),
])

Comparison_color = OrderedDict([
   ("Uber > YellowTaxi", "#1ebad6"),
   ("Uber < YellowTaxi", "#feecc0"),
])

clock_plot = figure(plot_width = width_clock, plot_height = height_clock,
                    x_axis_type = None, y_axis_type = None,
                    x_range=(-420, 420), y_range=(-420, 420),
                    min_border=0, outline_line_color="black",
                    background_fill_color="white")

clock_plot.xgrid.grid_line_color = None
clock_plot.ygrid.grid_line_color = None
    

#this is static part of the graph
clock_plot.annular_wedge(0, 0, inner_radius, outer_radius,'start_angles', 'angles', color = 'comparison_color',alpha = 0.5,source = TaxiTimeCount)

clock_plot.annular_wedge(0, 0, inner_radius, 'Uber_adjustedcount',
                'Uber_startangle', 'Uber_endangle',
                color = Taxi_color['Uber'], source = TaxiTimeCount)

clock_plot.annular_wedge(0, 0, inner_radius, 'YT_adjustedcount',
                'YT_startangle', 'YT_endangle',
                color=Taxi_color['YellowTaxi'],source = TaxiTimeCount)

# circular axes and lables
radii = np.linspace(320, 90, 5)
clock_plot.circle(0, 0, radius=radii, fill_color=None, line_color="white")
clock_plot.text(0, 'radii', 'label_num',source = lblclockdf, text_font_size="8pt", text_align="center", text_baseline="middle")

# radial axes
clock_plot.annular_wedge(0, 0, inner_radius-10, outer_radius+10,-big_angle+angles, -big_angle+angles, color="black")

# bacteria labels
Pickup_Hour = ['00:00-00:59','01:00-01:59','02:00-02:59','03:00-03:59','04:00-04:59','05:00-05:59','06:00-06:59','07:00-07:59','08:00-08:59','09:00-09:59','10:00-10:59','11:00-11:59','12:00-12:59','13:00-13:59','14:00-14:59','15:00-15:59','16:00-16:59','17:00-17:59','18:00-18:59','19:00-19:59','20:00-20:59','21:00-21:59','22:00-22:59','23:00-23:59','24:00-24:59']
xr = radii[0]*np.cos(np.array(-big_angle/2 + angles))
yr = radii[0]*np.sin(np.array(-big_angle/2 + angles))
label_angle=np.array(-big_angle/2+angles)
label_angle[label_angle < -np.pi/2] += np.pi # easier to read labels on the left side
clock_plot.text(xr, yr, Pickup_Hour , angle=label_angle,text_font_size="8.5pt", text_align="center", text_baseline="middle")

# legends
clock_plot.circle([135, 135], [-370, -390], color=list(Comparison_color.values()), radius=5)
clock_plot.text([-30, -30], [-370, -390],text=["Comparison: " + i for i in Comparison_color.keys()],text_font_size="10.5pt", text_align="center", text_baseline="middle")

clock_plot.rect([-40, -40, -40], [18, 0, -18], width=30, height=13,color=list(Taxi_color.values()))
clock_plot.text([-15, -15, -15], [18, 0, -18], text=list(Taxi_color),text_font_size="11pt", text_align="left", text_baseline="middle")

#############################################################################################################################################
#BUBBLE GRAPH
#initial value
UberDayCount,YTDayCount = bubble_graph(bor_categ[3],months[0])
CUberDayCount = ColumnDataSource(data = UberDayCount)
CYTDayCount = ColumnDataSource(data = YTDayCount)

Days = ['Mon', 'Tue', 'Wed', 'Thu', 'Fri', 'Sat', 'Sun']
DayTime = ['0-1', '2-3', '4-5', '6-7', '8-9', '10-11', '12-13', 
           '14-15', '16-17', '18-19', '20-21', '22-23']

Taxi_color = OrderedDict([
    ("Uber",   "#222233"),
    ("YellowTaxi", "#ff8400"),
])


bubbletips=[
    ("NumofPickups", "@AveDayCount")
]

bubble = figure(plot_width = width_bubble, 
           plot_height = height_bubble,
           x_range=Days,
           y_range=DayTime,
           tooltips = bubbletips    
           )

bubble.circle(x = 'AdjPosition', 
         y = 'AdjPickupHourGroup', 
         size = 'AdjAveDayCount', 
         source = CUberDayCount,
         color='#222233', 
         alpha = 0.8,     
        )
bubble.circle(x = 'AdjPosition', 
         y = 'AdjPickupHourGroup', 
         size = 'AdjAveDayCount',
         source = CYTDayCount,
         color='#ff8400',
         alpha = 0.8,     
        )
bubble.xaxis.axis_label = "Weekdays"
bubble.yaxis.axis_label = "DayTime"

label = figure(plot_width=120,
              plot_height=60,
              x_axis_type=None, 
              y_axis_type=None,
              x_range=(0,2),
              y_range=(0,2))


label.circle([0.2, 0.2], [1.5, 0.5], color=list(Taxi_color.values()), radius=0.1)

label.text([0.5, 0.5], [1.5, 0.5], text=[i for i in Taxi_color.keys()],
       text_font_size="11pt", text_align="left", text_baseline="middle")

bubble_layout = gridplot([[bubble, label]],toolbar_location=None)



#############################################################################################################################################
#WIDGETS and TOOLS
# Make a slider object: slider 
month_slider = Slider(title = 'Month',start = 1, end = 7, step = 1, value = 1)
month_slider.on_change('value', update_map)
month_slider.on_change('value', map_slider_interactions)


button = Button(label='► Play', width=60)
button.on_click(animate)
bor_geosource.selected.on_change('indices', map_slider_interactions)

tap_borough = TextInput(width = 300, value = bor_categ[3], title = 'Borough')
#############################################################################################################################################
# LAYOUT
layout_map = (gridplot([[row(map_plot, column(tap_borough, widgetbox(month_slider), button, color_bar_YT,color_bar_Uber,Text_tab3))], 
                        [row(clock_plot, bubble_layout)]],toolbar_location=None))

#############################################################################################################################################

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  # Remove the CWD from sys.path while we load stuff.


In [20]:
# Preparing data for Trend Graph

In [21]:
TaxiCount = Taxi

In [22]:
TaxiCount = pd.DataFrame(Taxi.groupby(['company_name', 'Pickup_Date','Days']).size()).reset_index()
TaxiCount.rename(columns={0: 'count'}, inplace=True)

In [23]:
TaxiCount['Uber'] = TaxiCount.loc[TaxiCount['company_name'] == 'Uber','count']
TaxiCount['YT'] = TaxiCount.loc[TaxiCount['company_name'] == 'YT','count']

In [24]:
YTdf = TaxiCount.loc[:,['YT','Pickup_Date']]
Uberdf = TaxiCount.loc[:,['Pickup_Date','Uber']]

In [25]:
Uberdf.dropna(inplace = True)
YTdf.dropna(inplace = True)

In [26]:
TaxiCount = pd.merge(Uberdf,YTdf,how = 'inner', on = 'Pickup_Date')

In [27]:
# Tab 1

In [28]:
# Introduction Text

In [29]:
Text = figure(plot_width=600, plot_height=300,
           min_border=0, x_range=(0,100), y_range=(0,100), 
           toolbar_location=None, title="Analysis of Competition Between Uber and Yellow Taxi")

Text.text(x=10, y=10, text_font_size = "12pt", text=["""
The engaging infographic illustrates the competition between 
incumbents and challengers of a market. This chart is created 
for the industry association of the yellow taxi in order to 
show how fierce competition is in the sector and to understand 
in which way it will be better to conduct lobbying activities.

The analysis represents the following goals:
  1) How competitors have get market traction over time
  2) Which areas of NYC have been affected the most
"""])


Text.title.text_font_size = "14pt"
Text.title.text_font_style = "bold"
Text.title.align = 'center'

Text.xaxis.visible = None
Text.yaxis.visible = None
Text.xgrid.grid_line_color = None
Text.ygrid.grid_line_color = None
Text.border_fill_color = None
Text.outline_line_color = None


In [30]:
# Trend Graph

In [31]:
source = ColumnDataSource(TaxiCount)

main_graph = figure(plot_width=800, plot_height=400, x_axis_type="datetime", 
                    x_range=(TaxiCount['Pickup_Date'].min(), TaxiCount['Pickup_Date'].max()), 
                    tools=('xpan, reset, save'), background_fill_color="white",
                    title = 'Number of Trips in NYC: Uber vs Yellow Taxi')

main_graph.title.align = 'center'
main_graph.yaxis.axis_label  = 'Number of Trips'

Uber_line = main_graph.line('Pickup_Date', 'Uber', source=source, legend_label="Uber", color='#1aa2bc')
YT_line = main_graph.line('Pickup_Date', 'YT', source=source, legend_label="Yellow Taxi", color='#ff8400')

main_graph.legend.location ="bottom_right"

main_graph.add_tools(HoverTool(tooltips=[("Uber", "@Uber"),('Date','@Pickup_Date{%F}')],
                      formatters={'Pickup_Date':'datetime'},
                      renderers=[Uber_line],
                      mode = "vline"))

main_graph.add_tools(HoverTool(tooltips=[("YT", "@YT"),('Date','@Pickup_Date{%F}')],
                      formatters={'Pickup_Date':'datetime'},
                      renderers=[YT_line],
                      mode = "vline"))

select = figure(title="Drag the middle and edges of the selection box to change the range above",
                plot_height=130, plot_width=800, y_range=main_graph.y_range,
                x_axis_type="datetime", y_axis_type=None,
                tools="", toolbar_location=None, background_fill_color="#ececec")



range_tool = RangeTool(x_range= main_graph.x_range)
range_tool.overlay.fill_color = "#848482"
range_tool.overlay.fill_alpha = 0.1

select.line('Pickup_Date', 'Uber', source=source, color='#1aa2bc')
select.line('Pickup_Date', 'YT', source=source, color='#febb1b')
select.ygrid.grid_line_color = None
select.add_tools(range_tool)
select.toolbar.active_multi = range_tool
select.add_tools(range_tool)

select.toolbar_location='below'

# LAYOUT
layout_count = (row(column(main_graph, select),Text))

In [32]:
#Preparing data for Regression

In [34]:
FHVr = FHV
YTr = YT
FHVr.rename(columns={'Pickup_DateTime': 'PUtime'}, inplace=True)
FHVr.rename(columns={'DropOff_datetime': 'DOtime'}, inplace=True)
FHVr['PUtime'] = pd.to_datetime(FHVr['PUtime'])
FHVr['DOtime'] = pd.to_datetime(FHVr['DOtime'])
YTr.rename(columns={'Pickup_DateTime': 'PUtime'}, inplace=True)
YTr.rename(columns={'DropOff_datetime': 'DOtime'}, inplace=True)
YTr['PUtime'] = pd.to_datetime(YTr['PUtime'])
YTr['DOtime'] = pd.to_datetime(YTr['DOtime'])

In [35]:
FHVr['day'] = FHVr['PUtime'].dt.day
FHVr['hour'] = FHVr['PUtime'].dt.hour
YTr['day'] = YTr['PUtime'].dt.day
YTr['hour'] = YTr['PUtime'].dt.hour

In [36]:
FHVr['day_of_week'] = FHVr['PUtime'].dt.weekday_name
FHVr['Date'] = FHVr['PUtime'].dt.date
YTr['day_of_week'] = YTr['PUtime'].dt.weekday_name
YTr['Date'] = YTr['PUtime'].dt.date

DataFrame creation with the variables used in regression

Factor Variables:

* day = 1
* night = 0
---------------------------------------------------------------------------------------------
* holiday = 1
* no holiday = 0
---------------------------------------------------------------------------------------------
* weekend = 1 (Friday-Sunday)
* weekday = 0

In [37]:
FHVgr = FHVr.groupby(['Date','hour', 'day', 'day_of_week'])['PUtime'].agg('count').reset_index(name = 'count')

YTgr = YTr.groupby(['Date','hour', 'day', 'day_of_week'])['PUtime'].agg('count').reset_index(name = 'count')

In [38]:
FHVgr['bind'] = 0
FHVgr.loc[(FHVgr['day_of_week'] == 'Friday') | (FHVgr['day_of_week'] == 'Saturday') | (FHVgr['day_of_week'] == 'Sunday'),'bind'] = 1

YTgr['bind'] = 0
YTgr.loc[(YTgr['day_of_week'] == 'Friday') | (YTgr['day_of_week'] == 'Saturday') | (YTgr['day_of_week'] == 'Sunday'),'bind'] = 1

In [39]:
FHVgr['binh'] = 0
FHVgr.loc[(FHVgr['hour']>6) & (FHVgr['hour']<18),'binh'] = 1

In [40]:
YTgr['binh'] = 0
YTgr.loc[(YTgr['hour']>6) & (YTgr['hour']<18),'binh'] = 1

In [41]:
FHVgr = FHVgr.groupby(['Date','day', 'binh', 'bind'])['count'].agg(sum).reset_index()
FHVgr['Date'] = pd.to_datetime(FHVgr['Date'])

YTgr = YTgr.groupby(['Date','day', 'binh', 'bind'])['count'].agg(sum).reset_index()
YTgr['Date'] = pd.to_datetime(YTgr['Date'])

In [42]:
w = pd.read_csv('Data/neweather.csv', sep=',')
w['Date'] = pd.to_datetime(w['Date'])

In [43]:
regrU = pd.merge(FHVgr, w, left_index=True, right_index=True)
regrU = regrU.drop(columns=['Date_x', 'Date_y'])

regrYT = pd.merge(YTgr, w, left_index=True, right_index=True)
regrYT = regrYT.drop(columns=['Date_x', 'Date_y'])

In [44]:
corrMatrixU = regrU.corr()
corrMatrixYT = regrYT.corr()

In [88]:
print(corrMatrixU)

              day      binh      bind     count       max       min    Precip  \
day      1.000000  0.000000 -0.025787 -0.038144  0.018557  0.028811 -0.080608   
binh     0.000000  1.000000  0.000000 -0.157301  0.000000  0.000000  0.000000   
bind    -0.025787  0.000000  1.000000  0.527947 -0.022401 -0.007387 -0.005210   
count   -0.038144 -0.157301  0.527947  1.000000 -0.391452 -0.398428  0.039097   
max      0.018557  0.000000 -0.022401 -0.391452  1.000000  0.948502 -0.175140   
min      0.028811  0.000000 -0.007387 -0.398428  0.948502  1.000000 -0.127302   
Precip  -0.080608  0.000000 -0.005210  0.039097 -0.175140 -0.127302  1.000000   
holiday -0.031857  0.000000 -0.123449 -0.077010 -0.069297 -0.041342 -0.035810   

          holiday  
day     -0.031857  
binh     0.000000  
bind    -0.123449  
count   -0.077010  
max     -0.069297  
min     -0.041342  
Precip  -0.035810  
holiday  1.000000  


In [89]:
print(corrMatrixYT)

              day      binh      bind     count       max       min    Precip  \
day      1.000000  0.000000 -0.025787 -0.066092  0.018557  0.028811 -0.080608   
binh     0.000000  1.000000  0.000000  0.509081  0.000000  0.000000  0.000000   
bind    -0.025787  0.000000  1.000000  0.054447 -0.022401 -0.007387 -0.005210   
count   -0.066092  0.509081  0.054447  1.000000  0.138070  0.109688 -0.236633   
max      0.018557  0.000000 -0.022401  0.138070  1.000000  0.948502 -0.175140   
min      0.028811  0.000000 -0.007387  0.109688  0.948502  1.000000 -0.127302   
Precip  -0.080608  0.000000 -0.005210 -0.236633 -0.175140 -0.127302  1.000000   
holiday -0.031857  0.000000 -0.123449 -0.205647 -0.069297 -0.041342 -0.035810   

          holiday  
day     -0.031857  
binh     0.000000  
bind    -0.123449  
count   -0.205647  
max     -0.069297  
min     -0.041342  
Precip  -0.035810  
holiday  1.000000  


In [45]:
mask = np.random.rand(len(regrU)) < 0.97
regr_trainU = regrU[mask]
regr_testU = regrU[~mask]
print ('Training data set length =' + str(len(regr_trainU)))
print('Testing data set length='+str(len(regr_testU)))

Training data set length =406
Testing data set length=18


In [46]:
expr = """count ~ binh + bind + Precip + min + max + holiday"""
y_trainU, X_trainU = dmatrices(expr, regr_trainU, return_type='dataframe')
y_testU, X_testU = dmatrices(expr, regr_testU, return_type='dataframe')
po_training_resultsU = sm.GLM(y_trainU, X_trainU, family=sm.families.Poisson()).fit()
print(po_training_resultsU.summary())
print(po_training_resultsU.mu)

                 Generalized Linear Model Regression Results                  
Dep. Variable:                  count   No. Observations:                  406
Model:                            GLM   Df Residuals:                      399
Model Family:                 Poisson   Df Model:                            6
Link Function:                    log   Scale:                          1.0000
Method:                          IRLS   Log-Likelihood:            -1.1315e+05
Date:                Thu, 19 Dec 2019   Deviance:                   2.2142e+05
Time:                        17:04:28   Pearson chi2:                 2.23e+05
No. Iterations:                     4                                         
Covariance Type:            nonrobust                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     10.3461      0.001   8421.648      0.0

In [47]:
regr_trainU['Lambda'] = po_training_resultsU.mu
regr_trainU['OLS_dep'] = regr_trainU.apply(lambda x: ((x['count'] - x['Lambda'])**2 - x['count']) / x['Lambda'], axis=1)

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [48]:
ols_expr = """OLS_dep ~ Lambda - 1"""
olsr_resultsU = smf.ols(ols_expr, regr_trainU).fit()
print(olsr_resultsU.params)

Lambda    0.020583
dtype: float64


In [49]:
nb2u_training_results = sm.GLM(y_trainU, X_trainU, family=sm.families.NegativeBinomial(alpha=olsr_resultsU.params[0])).fit()
print(nb2u_training_results.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:                  count   No. Observations:                  406
Model:                            GLM   Df Residuals:                      399
Model Family:        NegativeBinomial   Df Model:                            6
Link Function:                    log   Scale:                          1.0000
Method:                          IRLS   Log-Likelihood:                -3916.5
Date:                Thu, 19 Dec 2019   Deviance:                       397.65
Time:                        17:04:28   Pearson chi2:                     399.
No. Iterations:                     6                                         
Covariance Type:            nonrobust                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept     10.3588      0.029    354.439      0.0

In [51]:
nb2_predictions = nb2u_training_results.get_prediction(X_testU)
predictions_summary_frameU = nb2_predictions.summary_frame()
print(predictions_summary_frameU)

             mean      mean_se  mean_ci_lower  mean_ci_upper
9    20348.632749   362.497062   19650.411835   21071.662937
40   21442.722694   425.640146   20624.503152   22293.402810
60   29024.890408   432.244665   28189.950895   29884.559442
71   25110.119388   457.744682   24228.794542   26023.502513
85   27291.380617   389.292704   26538.948026   28065.146187
122  24653.200891   306.397699   24059.927558   25261.103247
129  28338.204722   403.669393   27557.969665   29140.530186
161  24367.066871   321.680019   23744.672358   25005.775566
223  25006.102946   404.506115   24225.721872   25811.622368
246  28988.555745   517.109146   27992.553316   30019.996914
283  29420.503748   387.753228   28670.253236   30190.387007
288  25078.382768   406.931826   24293.360306   25888.772666
316  27129.843903   398.338793   26360.240960   27921.915863
333  24278.711390   327.153682   23645.895190   24928.463145
338  31670.356570  1030.593853   29713.497031   33756.090178
380  32434.004560   486.

In [52]:
mask = np.random.rand(len(regrYT)) < 0.97
regr_trainYT = regrYT[mask]
regr_testYT = regrYT[~mask]
print ('Training data set length =' + str(len(regr_trainYT)))
print('Testing data set length='+str(len(regr_testYT)))

Training data set length =419
Testing data set length=5


In [53]:
expr = """count ~ binh + bind + Precip + min + max + holiday"""
y_trainYT, X_trainYT = dmatrices(expr, regr_trainYT, return_type='dataframe')
y_testYT, X_testYT = dmatrices(expr, regr_testYT, return_type='dataframe')
po_training_resultsYT = sm.GLM(y_trainYT, X_trainYT, family=sm.families.Poisson()).fit()
print(po_training_resultsYT.summary())
print(po_training_resultsYT.mu)

                 Generalized Linear Model Regression Results                  
Dep. Variable:                  count   No. Observations:                  419
Model:                            GLM   Df Residuals:                      412
Model Family:                 Poisson   Df Model:                            6
Link Function:                    log   Scale:                          1.0000
Method:                          IRLS   Log-Likelihood:                -92601.
Date:                Thu, 19 Dec 2019   Deviance:                   1.8024e+05
Time:                        17:04:29   Pearson chi2:                 1.77e+05
No. Iterations:                     4                                         
Covariance Type:            nonrobust                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      9.9017      0.001   7392.190      0.0

In [54]:
regr_trainYT['Lambda'] = po_training_resultsYT.mu
regr_trainYT['OLS_dep'] = regr_trainYT.apply(lambda x: ((x['count'] - x['Lambda'])**2 - x['count']) / x['Lambda'], axis=1)

/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.
/home/ubuntu/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [55]:
ols_expr = """OLS_dep ~ Lambda - 1"""
olsr_resultsYT = smf.ols(ols_expr, regr_trainYT).fit()
print(olsr_resultsYT.params)

Lambda    0.017538
dtype: float64


In [56]:
nb2y_training_results = sm.GLM(y_trainYT, X_trainYT, family=sm.families.NegativeBinomial(alpha=olsr_resultsYT.params[0])).fit()
print(nb2y_training_results.summary())

                 Generalized Linear Model Regression Results                  
Dep. Variable:                  count   No. Observations:                  419
Model:                            GLM   Df Residuals:                      412
Model Family:        NegativeBinomial   Df Model:                            6
Link Function:                    log   Scale:                          1.0000
Method:                          IRLS   Log-Likelihood:                -3981.7
Date:                Thu, 19 Dec 2019   Deviance:                       492.72
Time:                        17:04:29   Pearson chi2:                     473.
No. Iterations:                     6                                         
Covariance Type:            nonrobust                                         
                 coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------
Intercept      9.8963      0.027    371.870      0.0

In [58]:
nb2_predictions = nb2y_training_results.get_prediction(X_testYT)
predictions_summary_frameYT = nb2_predictions.summary_frame()
print(predictions_summary_frameYT)

             mean     mean_se  mean_ci_lower  mean_ci_upper
208  18685.793320  309.422653   18089.071897   19302.199361
219  24783.963660  307.629085   24188.296775   25394.299582
257  24762.811371  474.033574   23850.936167   25709.549625
360  21052.749113  263.802069   20542.004023   21576.193088
382  21275.226795  265.031442   20762.064842   21801.072226


In [ ]:
# Tab 2

In [59]:
Text_regression = figure(plot_width=1200, plot_height=300,
           min_border=0, x_range=(0,100), y_range=(0,100), 
           toolbar_location=None)

Text_regression.text(x=20, y=60, text_font_size = "12pt", text=["""
The regression model was created to analyze the most important factors affecting the demand.
The predictor variables used: day or night, weekend or not, holiday or not, precipitation, min and max temperature.
From the graphs above it can be seen that the model predicts demand well compared to actual data. 
"""])


Text_regression.title.text_font_size = "14pt"
Text_regression.title.text_font_style = "bold"
Text_regression.title.align = 'center'

Text_regression.xaxis.visible = None
Text_regression.yaxis.visible = None
Text_regression.xgrid.grid_line_color = None
Text_regression.ygrid.grid_line_color = None
Text_regression.border_fill_color = None
Text_regression.outline_line_color = None

In [60]:
from bokeh.layouts import gridplot
from bokeh.plotting import figure, show, output_notebook, output_file
from bokeh.layouts import widgetbox, row, column, layout
from bokeh.io import curdoc

predicted_countsU = predictions_summary_frameU['mean']
actual_countsU = y_testU['count']

predicted_uber = figure(title="Predicted vs Actual number of Uber pickups ", plot_height=400)

predicted_uber.circle(X_testU.index, predicted_countsU, legend_label="Predicted", color='#1EBAD6')
predicted_uber.circle(X_testU.index, actual_countsU, legend_label="Actual", color='#3b3a4a')

predicted_uber.line(X_testU.index, predicted_countsU, line_width=3, line_alpha=0.6, color='#1EBAD6', legend_label='Predicted')
predicted_uber.line(X_testU.index, actual_countsU, line_width = 3, line_alpha=0.6, color='#3b3a4a', legend_label='Actual')

predicted_uber.yaxis.axis_label = 'Number of pickups'

predicted_uber.legend.location ="bottom_right"

predicted_countsYT = predictions_summary_frameYT['mean']
actual_countsYT = y_testYT['count']

predicted_YT = figure(title="Predicted vs Actual number of Yellow Taxi pickups ", plot_height=400)

predicted_YT.circle(X_testYT.index, predicted_countsYT, legend_label="Predicted", color='#febb1b')
predicted_YT.circle(X_testYT.index, actual_countsYT, legend_label="Actual", color='#3b3a4a')

predicted_YT.line(X_testYT.index, predicted_countsYT, line_width=3, line_alpha=0.6, color='#febb1b', legend_label='Predicted')
predicted_YT.line(X_testYT.index, actual_countsYT, line_width = 3, line_alpha=0.6, color='#3b3a4a', legend_label='Actual')

predicted_YT.yaxis.axis_label = 'Number of pickups'
predicted_YT.legend.location ="bottom_right"

#layout_regression = (row(column(predicted_uber),column(predicted_YT)), row(Text_regression))
layout_regression = layout([
    [predicted_uber,predicted_YT],
    [Text_regression]])


In [ ]:
# Creating Tabs 

In [86]:
tab1 = Panel(child = layout_count, title="General Trend")
tab2 = Panel(child = layout_regression, title="Regression")
tab3 = Panel(child = layout_map, title="Map and Detailed Analysis")
tabs = Tabs(tabs=[tab1, tab2, tab3])

curdoc().add_root(tabs)

In [87]:
#output_notebook()
#show(tabs)

Loading BokehJS ...

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html

